In [2]:
import opendatasets as od

In [4]:
od.download('https://www.kaggle.com/datasets/cryptexcode/mpst-movie-plot-synopses-with-tags')

100%|██████████| 28.8M/28.8M [00:07<00:00, 3.81MB/s]


In [6]:
import pandas as pd
df = pd.read_csv('mpst-movie-plot-synopses-with-tags\mpst_full_data.csv')

In [7]:
df.head()

imdb_id                                          title  \
0  tt0057603                        I tre volti della paura   
1  tt1733125  Dungeons & Dragons: The Book of Vile Darkness   
2  tt0033045                     The Shop Around the Corner   
3  tt0113862                             Mr. Holland's Opus   
4  tt0086250                                       Scarface   

                                       plot_synopsis  \
0  Note: this synopsis is for the orginal Italian...   
1  Two thousand years ago, Nhagruul the Foul, a s...   
2  Matuschek's, a gift store in Budapest, is the ...   
3  Glenn Holland, not a morning person by anyone'...   
4  In May 1980, a Cuban man named Tony Montana (A...   

                                                tags  split synopsis_source  
0          cult, horror, gothic, murder, atmospheric  train            imdb  
1                                           violence  train            imdb  
2                                           romantic   test            imdb  
3             inspiring, romantic, stupid, feel-good  train            imdb  
4  cruelty, murder, dramatic, cult, violence, atm...    val            imdb

In [ ]:
!pip install gpt-2-simple

In [21]:
df.columns

Index(['imdb_id', 'title', 'plot_synopsis', 'tags', 'split',
       'synopsis_source'],
      dtype='object')

In [40]:
import numpy as np
from sklearn.model_selection import train_test_split
from tensorflow.keras.preprocessing.text import Tokenizer
from tensorflow.keras.preprocessing.sequence import pad_sequences
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Embedding, LSTM, Dense,  Flatten
from sklearn.preprocessing import MultiLabelBinarizer

In [23]:
df = df[['title', 'plot_synopsis', 'tags']]

In [63]:
tokenizer = Tokenizer()
tokenizer.fit_on_texts(df['title'])
title_sequences = tokenizer.texts_to_sequences(df['title'])
max_title_length = max(len(seq) for seq in title_sequences)
title_sequences = pad_sequences(title_sequences, maxlen=max_title_length)

In [64]:
tags = [tag.split(', ') for tag in df['tags']]
mlb = MultiLabelBinarizer()
tags = mlb.fit_transform(tags)

In [65]:
tokenizer_json = tokenizer.to_json()
with open('tokenizer.json', 'w') as json_file:
    json_file.write(tokenizer_json)

In [42]:
X_train, X_test, y_train, y_test = train_test_split(title_sequences, tags, test_size=0.2, random_state=42)

In [43]:
vocab_size = len(tokenizer.word_index) + 1
embedding_dim = 100

In [46]:

model = Sequential()
model.add(Embedding(vocab_size, embedding_dim, input_length=max_title_length))
model.add(LSTM(100))
model.add(Dense(tags.shape[1], activation='sigmoid'))

model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])


model.fit(X_train, y_train, batch_size=64, epochs=15, validation_data=(X_test, y_test))


Train on 11862 samples, validate on 2966 samples
Epoch 1/15
11862/11862 [==============================] - 10s 826us/sample - loss: 0.1911 - accuracy: 0.9457 - val_loss: 0.1417 - val_accuracy: 0.9569
Epoch 2/15
11862/11862 [==============================] - 11s 887us/sample - loss: 0.1390 - accuracy: 0.9583 - val_loss: 0.1416 - val_accuracy: 0.9569
Epoch 3/15
11862/11862 [==============================] - 11s 941us/sample - loss: 0.1388 - accuracy: 0.9583 - val_loss: 0.1415 - val_accuracy: 0.9569
Epoch 4/15
11862/11862 [==============================] - 11s 916us/sample - loss: 0.1367 - accuracy: 0.9583 - val_loss: 0.1420 - val_accuracy: 0.9568
Epoch 5/15
11862/11862 [==============================] - 11s 906us/sample - loss: 0.1310 - accuracy: 0.9595 - val_loss: 0.1433 - val_accuracy: 0.9567
Epoch 6/15
11862/11862 [==============================] - 11s 909us/sample - loss: 0.1248 - accuracy: 0.9608 - val_loss: 0.1444 - val_accuracy: 0.9569
Epoch 7/15
11862/11862 [=====================

In [47]:
model.save('story_gen.h5')

In [59]:
title = "A oversized t-shirt"


In [60]:
title_sequences = tokenizer.texts_to_sequences(title)

In [ ]:
predictions = model.predict(title_sequences)

In [75]:
from tensorflow.keras.models import load_model
with open('tokenizer.json', 'r') as f:
    tokenizer = tokenizer_from_json(f.read())

model = load_model('story_gen.h5')  

example_title = "Spider Man"

example_sequence = tokenizer.texts_to_sequences([example_title])
example_sequence = pad_sequences(example_sequence, maxlen=max_title_length)

predictions = model.predict(example_sequence)

predicted_tags = mlb.inverse_transform((predictions > 0.5).astype(int))

print("Input Title:", example_title)
print("Predicted Tags:", predicted_tags)

Input Title: Spider Man
Predicted Tags: [('murder',)]
